#  Описание работы

## Задания
* Идеи, что можно сделать с пропущенными отсчётами:
    1. [Теорема Котельникова](https://ru.wikipedia.org/wiki/%D0%A2%D0%B5%D0%BE%D1%80%D0%B5%D0%BC%D0%B0_%D0%9A%D0%BE%D1%82%D0%B5%D0%BB%D1%8C%D0%BD%D0%B8%D0%BA%D0%BE%D0%B2%D0%B0)
* Оптимизировать работу кода, задейстовав все возможные потоки процессора - [параллельное программирование](https://www.youtube.com/watch?v=fKl2JW_qrso&list=RDCMUCCezIgC97PvUuR4_gbFUs5g&start_radio=1&rv=fKl2JW_qrso&t=28)
* Проверить корректность работы ЕМ-алгоритма:
    * В окне довожу ЕМ до точности $\varepsilon$. Не сдвигая окно запускаю ЕМ ещё раз, но с новыми начальными приближениями. Так делаю 10 раз, сохраняя информацию о нач. прибл-ях. Добавляю 11-ым набором предпоследние, 10-ые, начальные приближения с последнего окна и выбираю тот набор, который максимизирует функцию правдоподобия. Результат - более точная (уверенная) максимизация функции правдоподобия (более точное разделение смесей).   

## Информация от физиков

1. Новый ЕМ дает много скачков из-за того, что сваливается не в те разные локальные минимумы (пере/недо-обучение, если можно так сказать). Чтобы поптаться это исправить, нужно в ЕМ отправлять значения параметров из предыдущего окна вместе с новыми, случайно-сгенерированными параметрами $\mu,\sigma,p$

### Памятка


* [number types](https://numpy.org/devdocs/user/basics.types.html).
* [plotly 3D](https://plotly.com/python/3d-charts/)
* [plotly documentation](https://plotly.github.io/plotly.py-docs/index.html)
* [plotly fig layout](https://plotly.com/python/reference/layout/#layout-title)
* [генератор политры цвета](https://coolors.co/092327-0b5351-00a9a5-4e8098-90c2e7)

# Загрузка данных

In [1]:
from pandas import read_csv
import numpy as np


# Позволяет использовать измененные модули без перезагрузки ядра
%load_ext autoreload
%autoreload 2

data_clean = read_csv('nice_jan_march')
data_clean.head()

Unnamed: 0.1  Unnamed: 0    BX    BY    BZ  Vx_Velocity  Vy_Velocity  \
0             0           1 -2.80  4.24  0.64       -593.8        -16.4   
1             1           2 -3.26  3.57 -0.71       -586.9        -12.7   
2             2           3 -3.71  3.23 -0.12       -583.8        -11.5   
3             3           4 -3.97  3.31  0.60       -585.8        -12.9   
4             4           5 -2.68  4.15  0.70       -575.2         -2.0   

   Vz_Velocity           ydhm_id  
0        -42.6  2023-01-01T00:01  
1        -28.3  2023-01-01T00:02  
2        -10.6  2023-01-01T00:03  
3        -44.5  2023-01-01T00:04  
4        -31.1  2023-01-01T00:05

# Обработка периода Январь-Март

В связи упомянутым замечанием про отсутсвие данных с периода Февраль-Июнь и построенным графиком всех данных, анализ данных будет осуществляться на подвыборке Январь-Март

## Визуализация данных

### Временные ряды и их гистограммы

In [19]:
from monitor import show_genral_info

show_genral_info(
    series=data_clean['BX'],
    add_title="Пропуски \"склеены\".",
    add_xaxis=data_clean['ydhm_id']
    )

Комментарии:
1. Склеенные данные не выглядят сплошными из-за равномерности сетки по времени. На самом деле в "дырках" отсчетов нет

### 3D гистограммы временных рядов

Here is code for 3D histogram visualization. It is implemented into 
DynamicMixture class as you will see later.

In [18]:
def hist3D(
        data, 
        window_size, 
        bins, 
        step
        ):
    
    def construct_hist3D(
            data, 
            window_size, 
            bins, 
            step
            ):
        """
        Функция составляет 3D гистограммы.

        Параметры
        ----------
        data : pandas.core.series.Series
            Колонка таблицы pandas.core.frame.DataFrame.
        window_size : int
            Длина поднабора (окна) data, который будет использоваться при анализе.
        bins : int
            Ширина ячейки гистограммы.
        step : int
            Величина смещения окна, относительно предыдущего.

        Возвращает:
        ----------
        df: pandas.core.frame.DataFrame
            Таблица с координатами точек привязок: bins, wind_numb, -
            и высотами столбцов - hist_freq.
            df.attrs: dict
                Содержит вспомогательную информацию, используемую при кастомизации.
        """
        from pandas import DataFrame
        from numpy import histogram, meshgrid
        
        num_windows = len(data) - window_size + 1
        #file_save_name = f"{data.name}-l{len(data)}-ws{window_size}-s{step}-b{bins}"
        df = DataFrame({'bins':[], 'wind_numb':[], 'hist_freq':[]})

        df.attrs = {"data_name": data.name,
                    "data_length": len(data),
                    "window_size": window_size,
                    "step_size": step,
                    "bin_size": bins}
        
        for i in range(0, num_windows, step):
            window = data[i:i+window_size]
            hist, _bins = histogram(window, bins=bins)
            xpos, ypos = meshgrid(_bins[:-1], i)
            xpos = xpos.flatten()
            ypos = ypos.flatten()
            dz = hist.flatten()
            df.loc[len(df.index)-1] = [xpos, ypos, dz]


            
        return df
    
    def visualize_3D_hist(hist3D):
        '''
        Строит объемный график, представляющий динамику изменения гистограмм в 
        зависимости от положения окна. Сечение, перпендикулярное оси y "№ Окна" - 
        это гистограмма в соответсвующем окне.
        '''
        import plotly.graph_objects as go

        # Выделение данных
        x = hist3D['bins'].values
        y = hist3D['wind_numb'].values
        z = hist3D['hist_freq'].values

        # Построение 3D поверхности
        fig = go.Figure(
            data=[
                go.Surface(
                    z=z, 
                    x=x, 
                    y=y)
                ]
            )

        # Персонализация изолиний и проекции
        custom_contours_z = dict(
            show=True,
            usecolormap=True,
            highlightcolor="limegreen",
            project_z=True
        )
        fig.update_traces(contours_z = custom_contours_z)

        # Персонализация осей
        custom_scene = dict(
            xaxis = dict(
                title='Интервалы гист-ы',
                color='grey'
                ),
            yaxis = dict(
                title='№ Окна',
                color='grey'
                ),
            zaxis = dict(
                title = 'Приращения ' + hist3D.attrs.get('data_name')+", нТ",
                color = 'grey'
                )
            )

        # Название графика
        custom_title = f"Компонента: {hist3D.attrs.get('data_name')}, " \
                f"кол-во данных: {hist3D.attrs.get('data_length')}, " \
                f"размер окна: {hist3D.attrs.get('window_size')}, "\
                f"кол-во интервалов {hist3D.attrs.get('bin_size')}, " \
                f"длина шага: {hist3D.attrs.get('step_size')}."
        
        # Персонализация графика
        fig.update_layout(title=custom_title,
                        scene=custom_scene,
                        autosize=True,
                        width=1200, height=600,
                        margin=dict(l=65, r=50, b=65, t=90))
        return fig
    
    return visualize_3D_hist(construct_hist3D(data, window_size, bins, step))

hist3D(data_clean['BX'][:9000], window_size=4300, step=30, bins=40).show()
hist3D(data_clean['BY'][:9000], window_size=4300, step=30, bins=40).show()
hist3D(data_clean['BZ'][:9000], window_size=4300, step=30, bins=40).show()

# ЕМ-алгоритм

### Desctiption

* __Е-этап__
    1. Calculate unnormalized responsibilities: 
    $$
    \normalsize{ \quad \tilde\rho_k^{[i]} = \pi_k \cdot \frac{1}{\sigma_k \sqrt{2\pi}} \cdot \exp{\left(-\frac{(x^{[i]} - \mu_k)^2}{2\sigma^2}\right)} \equiv
    \pi_k \cdot \frac{1}{\sigma_k} \cdot \varphi \left(\frac{x^{[i]} - \mu_k}{2\sigma} \right) }
    $$
    2. Normilize responsibilities: 
    $$
    \normalsize{ \quad \rho_k^{[i]} = \frac{\tilde\rho_k^{[i]}}{\sum_{k=0}^{M-1} \tilde\rho_k^{[i]}} }
    $$
    3. Calculate class responsibilities: 
    $$
    \normalsize{ \quad \gamma_k = \sum_{i=0}^{N-1} \rho_k^{[i]} }
    $$
* __М-этап__
    1. Update the class probabilities: 
    $$
    \normalsize{ \quad \pi_k = \frac{\quad \gamma_k}{N} }
    $$
    2. Update the math. expectations: 
    $$
    \normalsize{ \quad \mu_k = \frac{1}{\gamma_k} \cdot \sum_{i=0}^{N-1} \rho_k^{[i]}x^{[i]} }
    $$
    3. Update the standard deviations:
    $$
    \normalsize{ \quad \sigma_k = \sqrt{\frac{1}{\gamma_k} \cdot \sum_{i=0}^{N-1} \rho_k^{[i]}\left(x^{[i]} - \mu_k \right)^2} }
    $$

In [6]:
import tensorflow_probability
from Mixture import mixture

### Generate mixture, check EMs on valid initial parameters, compare results 

In [7]:
# Create mixture model
m = mixture(
    num_comps=3,
    distrib=tensorflow_probability.distributions.Normal
    )
np.random.seed()
rseed = np.random.randint(1_000)
m.initialize_probs_mus_sigmas(random_seed=rseed)
print(f"radnom seed equal to {rseed}")
# Generate data for testing
m.generate_samples(1_000, random_seed=57)
another_data = m.construct_tpf_mixture().sample(1_000).numpy()
test_data1 = m.samples
test_data2 = another_data

## additional stuff; output appearancece
__round = lambda numb, dig=4: round(numb, dig)
Round = lambda lis, dig=4: list(map(lambda numb: round(numb, dig),lis))
custom_print = lambda text, *args, func=Round: print(
    text, 
    f"Orig - {func(args[0])}",
    f"Iter - {func(args[1])}",
    f"Adap - {func(args[2])}",
    sep='\n\t')

# EM comparison
pit, mit, sit, llhit = m.EM_iterative(test_data1, 30)
pad, mad, sad, llhad = m.EM_adaptive(test_data1, 0.001)

custom_print("Components probabilities:", m.probs, pit, pad)
custom_print("Mathematical expectations:", m.mus, mit, mad)
custom_print("Standard deviations:", m.sigmas, sit, sad)
custom_print("Log-likelihoods:", m.log_likelihood(test_data1), llhit, llhad, 
             func=__round)


radnom seed equal to 549
Components probabilities:
	Orig - [0.0165, 0.1351, 0.8483]
	Iter - [0.0162, 0.1407, 0.8431]
	Adap - [0.0162, 0.1414, 0.8424]
Mathematical expectations:
	Orig - [0.4821, 0.8082, 0.8307]
	Iter - [0.5885, 0.8842, 0.8126]
	Adap - [0.5928, 0.8884, 0.8117]
Standard deviations:
	Orig - [0.7, 0.6552, 0.9588]
	Iter - [0.6428, 0.6518, 0.9653]
	Adap - [0.6382, 0.6527, 0.9654]
Log-likelihoods:
	Orig - -1339.284
	Iter - -1339.1538
	Adap - -1339.1505


#### Checking sieving EM

In [122]:
np.random.seed()
rseed = np.random.randint(1_000)
m = mixture(
    num_comps=3,
    distrib=tensorflow_probability.distributions.Normal,
    random_seed=rseed,
    rand_initialize=True
    )

print(f"random seed equal to {rseed}")
# Generate data for testing
m.generate_samples(1_000, random_seed=rseed)

round_sort = lambda param, n: [round(elem, n) for elem in np.sort(param)]

# print("Original probs:",round_sort(m.probs, 4),'\n')
res = m.EM_sieving(
    m.samples, 
    iter_initial=8, 
    num_candid=50,
    num_best_candid=10,
    accur_final=0.001,
    random_seed=rseed)

print("Original mixture:",
      round_sort(m.probs, 4), 
      m.mus, 
      m.sigmas, 
      sep='\n')
print("Sieved EM result:", *res, sep='\n')
orig_mat = np.array([m.probs, m.mus, m.sigmas])
pred_mat = np.array([res[0], res[1], res[2]])
print("\nNorma for not sorded matrixes: ", np.linalg.norm(pred_mat - orig_mat))
print("\nDistance between originals and predictions - ", 
      round(
        np.linalg.norm(
            np.sort(m.__getattribute__('probs')) - 
            np.sort(res[0])
            ),
        4)
    )

random seed equal to 287
Original mixture:
[0.0448, 0.3559, 0.5993]
[0.77122738 0.22141908 0.01811318]
[5.77575665 1.16678944 5.18802513]
Sieved EM result:
[0.1240376  0.57153226 0.30443013]
[-1.35715499  0.21179299  0.56053755]
[1.01983683 5.3779924  0.87617865]
-2731.6292517007873

Norma for not sorded matrixes:  7.994315370103347

Distance between originals and predictions -  0.0985


# Reconstruction a(t) and b(t) coefficients as a time function

$\textbf{Задача 6}$. Реконструировать коэффициенты $a(t)$ и $b(t)$, то есть построить их «точечные» оценки
путем использования оценок распределений коэффициентов уравнения (1), полученных в резуль-
тате решения Задач 1 – 2, для построения оценок самих коэффициентов. В качестве таких оценок
берутся математическое ожидание и среднеквадратическое отклонение оцененного распределе-
ния:
$$
a(t) ≈ a(t) = \sum_{k=1}^{K}{p_k a_k}, \quad 
b(t) ≈ b(t) = \sum_{k=1}^{K}{p_k\cdot(b^{2}_k + a^{2}_k) − a(t)^2}
$$
Здесь t – время (положение окна), параметры $a_k , b_k , p_k$ также зависят от положения окна.

## Implemetation

In [4]:
from Mixture import DynamicMixture

2024-03-03 22:51:28.448907: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2024-03-03 22:51:28.682634: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-03 22:51:28.682878: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-03 22:51:28.723636: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-03 22:51:28.818249: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2024-03-03 22:51:28.819886: I tensorflow/core/platform/cpu_feature_guard.cc:1

In [14]:
STEP = 60

bx_mixture = DynamicMixture(
    num_comps=6,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

by_mixture = DynamicMixture(
    num_comps=6,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

bz_mixture = DynamicMixture(
    num_comps=6,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

vx_mixture = DynamicMixture(
    num_comps=6,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

vy_mixture = DynamicMixture(
    num_comps=6,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

vz_mixture = DynamicMixture(
    num_comps=6,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

MIXTURES = [
    bx_mixture, by_mixture, bz_mixture, 
    vx_mixture, vy_mixture, vz_mixture
    ]

bx = data_clean['BX'].values
by = data_clean['BY'].values
bz = data_clean['BZ'].values

vx = data_clean['Vx_Velocity'].values
vy = data_clean['Vy_Velocity'].values
vz = data_clean['Vz_Velocity'].values

TRACES = [
    bx, by, bz,
    vx, vy, vz
]

In [11]:
bx_mixture.predic_light(bx)


Deleted


Candidates generation:   0%|          | 0/30 [00:00<?, ?it/s]

ЕМ для лучших парам-ов:   0%|          | 0/8 [00:00<?, ?it/s]

  0%|          | 0/1246 [00:00<?, ?it/s]

Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  256
Bad selection in ADAP. Restarting the iteration  72
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  8
Bad selection in ADAP. Restarting the iteration  20
Bad selection in ADAP. Restarting the iteration  21
Bad selection in ADAP. Restarting the iteration  1
Bad selection in ADAP. Restarting the iteration  9
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  11
Bad selection in ADAP. Restarting the iteration  0
Bad selection in ADAP. Restarting the iteration  4
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  36
Bad selection in ADAP. Restarting the iteration  8


'finished'

In [153]:
vx_mixture = DynamicMixture(
    num_comps=3,
    distrib=tensorflow_probability.distributions.Normal,
    time_span=data_clean['ydhm_id'].values,
    window_shape=(4500, STEP))

vx_mixture.windows

[]

In [150]:
vx_mixture.show_hist_3d(bins=30).show()

In [13]:
from plotly.express import line
bx_mixture.reconstruct_process_coef()
line(bx_mixture.process_coefs).show()

# vx_mixture.reconstruct_process_coef()
# line(vx_mixture.process_coefs).show()

Deleted proc params


## For all at onec

In [16]:
for mixture, data in zip(MIXTURES, TRACES):
    # calculate parameters
    mixture.predic_light(data=data)

Deleted


Candidates generation:   0%|          | 0/30 [00:00<?, ?it/s]

ЕМ для лучших парам-ов:   0%|          | 0/8 [00:00<?, ?it/s]

  0%|          | 0/1246 [00:00<?, ?it/s]

Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  256
Bad selection in ADAP. Restarting the iteration  72
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  8
Bad selection in ADAP. Restarting the iteration  20
Bad selection in ADAP. Restarting the iteration  21
Bad selection in ADAP. Restarting the iteration  1
Bad selection in ADAP. Restarting the iteration  9
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  11
Bad selection in ADAP. Restarting the iteration  0
Bad selection in ADAP. Restarting the iteration  4
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  36
Bad selection in ADAP. Restarting the iteration  8
Deleted


...

Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  8
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  4
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  96
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  11
Bad selection in ADAP. Restarting the iteration  5
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  1
Bad selection in ADAP. Restarting the iteration  10
Bad selection in ADAP. Restarting the iteration  6
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  4
Bad selection in ADAP. Restarting the iteration  15
Bad selection in ADAP. Rest

Candidates generation:   0%|          | 0/30 [00:00<?, ?it/s]

ЕМ для лучших парам-ов:   0%|          | 0/8 [00:00<?, ?it/s]

  0%|          | 0/1246 [00:00<?, ?it/s]

Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  5
Bad selection in ADAP. Restarting the iteration  35
Bad selection in ADAP. Restarting the iteration  42
Bad selection in ADAP. Restarting the iteration  1
Bad selection in ADAP. Restarting the iteration  6
Bad selection in ADAP. Restarting the iteration  16
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  26
Bad selection in ADAP. Restarting the iteration  138
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  4
Bad selection in ADAP. Restarting the iteration  559
Bad selection in ADAP. Restarting the iteration  96
Bad selection in ADAP. Restarting the iteration  6
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  24
Bad selection in ADAP. Restarting the iteration  15
Bad selection in ADA

In [17]:
vy_mixture.predic_light(vy)

Deleted


Candidates generation:   0%|          | 0/30 [00:00<?, ?it/s]

ЕМ для лучших парам-ов:   0%|          | 0/8 [00:00<?, ?it/s]

  0%|          | 0/1246 [00:00<?, ?it/s]

Bad selection in ADAP. Restarting the iteration  16
Bad selection in ADAP. Restarting the iteration  34
Bad selection in ADAP. Restarting the iteration  0
Bad selection in ADAP. Restarting the iteration  23
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  158
Bad selection in ADAP. Restarting the iteration  22
Bad selection in ADAP. Restarting the iteration  25
Bad selection in ADAP. Restarting the iteration  1
Bad selection in ADAP. Restarting the iteration  8
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  26
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  14
Bad selection in ADAP. Restarting the iteration  13
Bad selection in ADAP. Restarting the iteration  7
Bad selection in ADAP. Restarting the iteration  2
Bad selection in ADAP. Restarting the iteration  3
Bad selection in ADAP

'finished'

In [18]:
COEFS = []
for mixture in MIXTURES:
    a,b = mixture.reconstruct_process_coef()
    coefs = dict(
        a=a,
        b=b
    )
    
    COEFS.append(coefs)

Deleted proc params
Deleted proc params
Deleted proc params
Deleted proc params
Deleted proc params
Deleted proc params


## Visualization: pictures

In [23]:
(vy_mixture.frame)

{'length': 4500, 'step': 60}

In [26]:
import plotly
plotly.graph_objs.Line(COEFS[0])

/home/oplora/Documents/VMK/Dissertation/Magfield/.venv/lib/python3.10/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




{'a': array([-0.67101778, -0.60429111, -0.5159    , ...,  3.54702444,
         3.48437556,  3.42118444]),
 'b': array([6.1625979 , 3.94275998, 3.75371288, ..., 4.15773563, 4.61163857,
        4.70990784])}

In [25]:
var_name = ['BX', 'BY', 'BZ', 'VX','VY','VZ']

for coefs,name in zip(COEFS, var_name):
    fig = line(coefs, title=name+" | dX(t) = a(t) dt + b(t) dW\t"+"| Window length=4500, step=60")
    fig.show()
    

## Draft section

In [ ]:
def procpar(pk,ak,bk):
    'for a specific window'
    a = np.sum(pk * ak)
    b = np.sum(pk * (bk**2 * ak**2) - a**2)
    return a, b

ar1 = np.array([1,2,3])
ar2 = np.array([7,-1,2])
procpar(ar1, ar2, 3)

(11, 204)

In [ ]:
get_ind = lambda i, dic: (dic['probs'][i], dic['mus'][i], dic['sigmas'][i])
res1 = get_ind(177, mixture.parameters)
res2 = get_ind(178, mixture.parameters)
res3 = get_ind(179, mixture.parameters)

In [ ]:
print(res1, '\n',res2, '\n',res3)

(array([0.02387807, 0.27504872, 0.70107321]), array([ 5.89462775, -2.34683612,  0.8787476 ]), array([0.46679448, 1.53790819, 1.54189323])) 
 (array([0.02388599, 0.69972019, 0.27639382]), array([ 5.89441944,  0.88096214, -2.34261927]), array([0.46694703, 1.54119456, 1.54988661])) 
 (array([0.02388731, 0.69942203, 0.27669066]), array([ 5.89440913,  0.88163954, -2.34312089]), array([0.46694914, 1.54079016, 1.55273918]))


Assume we have a matrix of same-size lists, that contains integer numbers, that 
correspond to some order of mixture parameters.
On each neighbouring windows we want to compare those matrixes to find out if
any parameters variables crossed each other and change raletive positions. 
For this case of course basic ordering (for example by increasing of standard
diviation) not working because this approach exclude oppartunity for 
this specific parameter to have intesetions between different components.

It means that we need to think of something trickier.
Let's try implenet next approach:
1. Initialize some integer values to track order. For expamle - get indexes of
increasing sorting of each array. And sort all values by one of the rows 
(for instance by sigmas). Thereupon save this values into matrix to ceep the track on.
2. Calculate values on next window, sort by previously chosen row, 
save them in new matrix and compare them to previous 'order matrix'.
3. If those matrixes are equal, then save current order matrix into previos and
move on step 2.
4. Otherwise at list one array differes at list by two values 

(example: 
$\quad[[1,2,0][0,2,1]\textbf{[0,1,2]}] vs [[1,2,0][0,2,1] \textbf{[2,1,0]}] \quad$
, - first and last arguments differes). 

Chance of two arrays change their values at the same time is orbitrary low (I think).
So if amended array is not on the same row that we are using for sorting, than \
we're fine. We've just tracked intersection. Move on step 2.
5.  However if this array is on the same row that we are sorting by, then there 
must be applied additional actions. We need to take other row from 'previous 
order matrix'. See how it correspond to originaly chosen row, save their
'relation' and resort current order matrix's original row. Other rows shouldn't
be altered!




Also it is obvious 
that only columns may switch their places. It means them there is no use in sorting values by line
I need to think of 'vertical' ordering. For ecamle I cand calculated initial orders and make dictionary of 
three elements: 'first line", ..,'third line'. All this elements will contain a 1-D vector.
And if the values changes than columns are switching. It means that 

In [ ]:
def order(*args):
    
    order_matrix = []
    indexs = range(len(args[0]))

    for arg in args:
        order_matrix.append(
            sorted(
                indexs,
                key=lambda k: arg[k]
                )
            )
    return order_matrix

def order_by(indexs, args):
    for arg in args:
        arg = np.array([arg[i] for i in indexs])
        print(arg)
def alter_order(
        ordmat_prev: list, 
        ordmat_cur: list
        ):
    from copy import deepcopy
    omp = deepcopy(ordmat_prev)
    omc = deepcopy(ordmat_cur)
    print(omp != omc)
    if omp != omc:
        print(omp, omc)
        omp.pop(-1)
        omc.pop(-1)
        if omp != omc:
            return omp.pop(-1)
        else:
            alter_order(omp, omc)
    # return omc.pop(-1)
        # if all([a_id == b_id for a_id, b_id in zip(omp, omc)]):

        

In [ ]:
res1

(array([0.02387807, 0.27504872, 0.70107321]),
 array([ 5.89462775, -2.34683612,  0.8787476 ]),
 array([0.46679448, 1.53790819, 1.54189323]))

In [ ]:
res2

(array([0.02388599, 0.69972019, 0.27639382]),
 array([ 5.89441944,  0.88096214, -2.34261927]),
 array([0.46694703, 1.54119456, 1.54988661]))

In [ ]:
ord1 = order(*res1)
ord2 = order(*res2)
alter_order(ord1,ord2)

True
[[0, 1, 2], [1, 2, 0], [0, 1, 2]] [[0, 2, 1], [2, 1, 0], [0, 1, 2]]


[1, 2, 0]

In [ ]:
order_by([1,2,0], res2)

[0.69972019 0.27639382 0.02388599]
[ 0.88096214 -2.34261927  5.89441944]
[1.54119456 1.54988661 0.46694703]


In [ ]:
res2

(array([0.02388599, 0.69972019, 0.27639382]),
 array([ 5.89441944,  0.88096214, -2.34261927]),
 array([0.46694703, 1.54119456, 1.54988661]))

In [ ]:
def swapes_ones(ar1, ar2):
    pairs = []
    for el1, el2 in zip(ar1,ar2):
        if (el1 == el2) or (any([el1 in pair for pair in pairs])):
            continue
        else:
            pairs.append([el1, el2])
    return pairs

def swap(pairs, arr):
    for i, ar in enumerate(arr):
        for par in pairs:
            if ar in par:

                par.remove(ar)
                print(int(par), ar)
                arr[i] = par



# Черновики

$$
\mathbb{D}Z = \mathbb{D}V + \mathbb{E}U^2
\newline
\mathbb{E}U^2 = \sum_{j=1}^{k}{\sigma_j^2 \cdot p_j} - 
    \text{диффузионная компонента}
\newline
\mathbb{D}V = \sum_{j=1}^{k}{(\mu_j - \bar{\mu}) \cdot p_j}, \quad \text{где} 
    \quad \bar{\mu} = \sum_{j=1}^{k}{\mu_j p_j}, - 
    \text{динамическая компонента}
$$

In [114]:
def diffusion_component(mixture):
    mus = mixture['math_exp'].values
    class_probs = mixture['cl_prob'].values
    total_mu = np.sum(mus * class_probs, axis=1, keepdims=True)
    return np.sum((mus-total_mu)**2 * class_probs, axis=1, keepdims=True)

def dynamic_component(mixture):
    sigmas = mixture['st_dev'].values
    class_probs = mixture['cl_prob'].values
    return np.sum(sigmas**2 * class_probs, axis=1, keepdims=True)

dicom = diffusion_component(mixture3)
dycom = dynamic_component(mixture3)

In [115]:
import plotly.express as px
px.line(dicom, title='Диффузионная компонента')

In [116]:
px.line(dycom, title='Динамическая компонента')

In [ ]:
def construct_mixture_2Dplot(data_multicol):
    '''
    График для вывода весов, мат.ож-ий и ср.кв.откл-ий для смесей распределений
    '''
    from plotly.graph_objects import Scatter # Для потсроения кривых   
    #from essentials import mixture
    from plotly.subplots import make_subplots
    
    # Создает соответсвующие названия для построение графиков (колонок)
    def custom_param_names(params):
        names = []
        for param in params:
            if param == 'cl_prob':
                names.append("Изменение весов компонент смеси")
            elif param == 'math_exp':
                names.append("Изменение математических ожиданий компонент смеси")
            elif param == 'st_dev':
                names.append("Изменение среднеквадратичных отклонений компонент смеси")
        return names
    
    # индексы измерений (всего их сколько и окон)
    X = data_multicol.attrs.get('custom_xaxis')
    
    lows = list(data_multicol.columns.levels[1]) # число законов в смеси
    lows.remove('')
    lows_colors = ["#84C318", "#C45AB3", "#EDD892",
                   "#C44536", "#4BB3FD", "#FC944A",
                   "#4AFC94", "#00A9A5"]
    
    params = list(data_multicol.columns.levels[0]) # число параметров для каждого закона
    params.remove('LL_hist')
    params_names = custom_param_names(params)
    params_names.append('Энтропия')
    params_names.append('Маргинальная log функция правдоподобия')
    
    num_rows =len(params)+1 + 1 # +1 для энтропии +1 для ф-ии лог-маргинального правдоподобия
    fig = make_subplots(rows=num_rows, cols=1,
                        subplot_titles=params_names,
                        row_titles=None,
                        vertical_spacing=0.24/num_rows)
    # Графики характеристик смесей
    for row_ind, parameter in enumerate(params):
        legend = True if row_ind==len(params)-1 else False
        for i, low in enumerate(lows):
            Y = data_multicol.loc[:,(parameter, low)].values
            fig.add_trace(Scatter(x=X, 
                                  y=Y,
                                  name=f"Закон №{i+1}",
                                  legendgroup=f"Закон №{i+1}",
                                  showlegend=legend,
                                  mode='lines', line=dict(
                                      color=lows_colors[i]),
                          hoverlabel=dict(font_color='blue')),
                          row = row_ind + 1,
                          col = 1,
                          )
    # График энтропии
    from essentials import entrophy
    entr = entrophy(data_multicol)
    fig.add_trace(Scatter(x=X, 
                          y=entr,
                          name=f"Энтропия",
                          showlegend=legend,
                          mode='lines', line=dict(
                              color=lows_colors[-1])),
                  row = num_rows - 1,
                  col = 1,
                  )
    
    # График функции правдоподобия
    Y = data_multicol.loc[:, 'LL_hist'].values
    fig.add_trace(Scatter(x=X, 
                          y=Y,
                          name=f"Фун-ия правдоподобия",
                          showlegend=legend,
                          mode='lines', line=dict(
                              color=lows_colors[-2])),
                  row = num_rows,
                  col = 1,
                  )
    
    # Название графика
    if data_multicol.attrs.get('num_of_iter') is not None:
        em_cond_description = f"Итераций {data_multicol.attrs.get('num_of_iter')}. "
    elif data_multicol.attrs.get('conv_prime') is not None:
        em_cond_description = f"Точность весов: {data_multicol.attrs.get('conv_prime')}. "
        
    custom_title = str(f"Смесь из {len(lows)} законов, "+
            f"{data_multicol.attrs.get('data_length')} отсчётов "+
            f"{data_multicol.attrs.get('data_name')}. "+
            f"Окно: {data_multicol.attrs.get('window_size')}. "+
            em_cond_description+
            f"Шаг: {data_multicol.attrs.get('step_size')}.")
    
    # Персонализация холста
    fig.update_layout(autosize=False,
                      xaxis_tickformatstops=TIME_RELATED_XTICK,
                      title=dict(text=custom_title,
                                 font=dict(size=22)),
                      template='plotly_dark',
                      legend = dict(font=dict(size=12,
                                              color="#000066"),
                                    bgcolor="#FFFFFF",
                                    bordercolor="#FF0000",
                                    borderwidth=2),
                      width=1000,
                      height=400*len(params)
                     )
    return fig